### Identification of entities: Query DBpedia Spotlight

### This notebook processes text from music personalities' biographies and extract historical meetups information 
#### We use DbPedia Spotlight for automatic identification and annotation of entities in text
#### Pre-requirements:
#### Text organised by sentences
#### A file containing one music personality biography organised by sentences
#### A local installation of DBpedia Spotlight
####  - Define parameters to query DBpedia Spotlight.
####  - Confidence 0.4
####  - Response format JSON

#### For each file
#### Named entity recognition
#### - Read file from indexedSentences/
#### - For each sentence in the file
####   - Use DBpedia Spotlight and annotate entities 
####   - Process JSON response and organise in CSV format
####   - Store information in cacheSpotlightResponse/ directory

#### Named entity recognition missing entities
#### DBpedia Spotlight returns the list of entities, however not all of them have an entity type
#### To ensure that we are not missing important entities (People and Place) we interrogate DBpedia for that particular entity and save the values in cache
#### For each file in cacheSpotlightResponse/
####   - Filter out entities with type
####   - Query Dbpedia for the entity and type
####   - Process JSON response and organise in CSV format
####   - Store the results in cacheSpotlightResponse/
####   - Maintain an entry with all the entity-types values returned

#### Directories information:
#### indexedSentences/ : collection of biographies in CSV format. Each row of the file represents a sentence. Each row has a section name and paragraph index, and sentence index
#### cacheSpotlightResponse/ : collection of biographies in CSV format. Each biography contains the list of entities identified using DBpedia Spotlight, each linked to its corresponding sentence

In [1]:
import json
import os
import pandas as pd
from _datetime import date
import time
from operator import itemgetter

# For DBpedia spotlight, PPE entities
import requests
import pycurl
from urllib.request import urlopen
from urllib.parse import quote

In [42]:
# reading every CSV with indexed sentences
# return a list object of files in the given folder
files_list = [f for f in os.listdir('indexedSentences') if not f.startswith('.')]
# parse to dataframe
df_files = pd.DataFrame(files_list, columns=['file_name'])
# df_files = df_files.query("file_name=='1903762.csv'")
df_files.to_csv('totalBiographiesEntities.csv',index=False)

df_files.info()
df_files.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 37155 entries, 0 to 37154
Data columns (total 1 columns):
 #   Column     Non-Null Count  Dtype 
---  ------     --------------  ----- 
 0   file_name  37155 non-null  object
dtypes: object(1)
memory usage: 290.4+ KB


file_name
0  10002116.csv
1   1000228.csv
2  10004137.csv
3   1000522.csv
4   1000539.csv

In [43]:
# extract only the ones that do not exist in folder
files_list = [f for f in os.listdir('cacheSpotlightResponse') if not f.startswith('.')]
# parse to dataframe
df_query = pd.DataFrame(files_list, columns=['file_name'])
df_result = df_files[~df_files['file_name'].isin(df_query['file_name'])]
df_files = df_result
df_files.to_csv('totalBiographiesEntities.csv',index=False)
df_files.info()
df_files.head()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1 entries, 296 to 296
Data columns (total 1 columns):
 #   Column     Non-Null Count  Dtype 
---  ------     --------------  ----- 
 0   file_name  1 non-null      object
dtypes: object(1)
memory usage: 16.0+ bytes


file_name
296  103566.csv

## 1. DBpedia Spotlight functions

In [6]:
# using DBPedia spotlight to search for entities
# URL for local installation of DBpedia spotlight
urlAnnotation = 'http://dbpedia-spotlight.en:80/rest/annotate/'
# urlAnnotation = 'http://dbpedia-spotlight.en:2222/rest/annotate/' ## not working

# if using KMi sparql endpoint
# urlAnnotation = 'https://whise.kmi.open.ac.uk/rest/annotate'

# setting headers and parameters not using DBpedia categories
def setDbPediaAnnotationServiceParameters(text):
    """ Se parameters for querying Dbpedia
    args: text - text to be analysed
    return: headers
            params
    """
    headers = {
        'Accept':'application/json',
        "content-type":"application/x-www-form-urlencoded"
    }

    params = {
        'confidence': '0.4',
        "text":text,
    }
    return headers, params

# setting headers and parameters, filtering by categories
def setDbPediaAnnotationServiceParametersTypes(text,types):
    """ Se parameters for querying Dbpedia
    args: text - text to be annotated
        types: different categories of entities
    return: headers
            params
    """
    headers = {
        'Accept':'application/json',
        "content-type":"application/x-www-form-urlencoded"
    }

    params = {
        'types' : types,
        'confidence': '0.35',
        "text":text,
    }
    return headers, params

# return response in JSON format
def queryDBPediaAnnotation(url,header,params):
    try:
        response = requests.post(url,headers=header, params=params).json()
        
    except Exception as ex:
        if hasattr(ex, 'message'):
            print(ex.message)
        else:
            print(ex)
        raise Exception(ex)
    # finally:
        # print(response)

    return response

def executeQueryDbpedia(q, f='application/json'):
    epr = "http://dbpedia.org/sparql"
    try:
        params = {'query': q}
        resp = requests.get(epr, params=params, headers={'Accept': f})
    #    return resp.text
        return resp
    except Exception as e:
        print(e, file=sys.stdout)
        raise

## 2. Query Dbpedia Spotlight

In [44]:
# use chunk to load a small number of files in memory
for chunk in pd.read_csv('totalBiographiesEntities.csv', chunksize=5):
    df_files = pd.DataFrame()
    df_files['file_name'] = chunk['file_name']

    # for each file/biography in the list, read its sentences 
    # and annotated the entities using the configured sparql endpoint
    for file_name in df_files.itertuples():
        # start = time.time()
        print(file_name.file_name)
        # Read file with segmented sentences
        biography_df = pd.read_csv('indexedSentences/'+file_name.file_name)
        df_entities = pd.DataFrame()

        # for each sentence in the biography
        for sentence_row in biography_df.itertuples():
            ## send sentence text and return params for query
            # passing as parameters: sentence text
            hdrs, prms = setDbPediaAnnotationServiceParameters(sentence_row.sentences)
            try:
                # obtain response using DBpedia spotlight: either local installation or KMi dbpedia sparql endpoint to query entities
                responseJSON = queryDBPediaAnnotation(urlAnnotation,hdrs,prms)
                # UPDATE: save responses from DBP Spotlight
                if 'Resources' in responseJSON:
                    file_exists = os.path.isfile('cacheSpotlightResponse/'+file_name.file_name)
                    df_resources = pd.DataFrame.from_dict(responseJSON['Resources'])
                    df_resources['sentence']=sentence_row.sentences
                    df_resources['sentenceIndex']=sentence_row.sentenceIndex
                    df_resources['paragraphIndex'] = sentence_row.paragraphIndex
                    df_resources['section'] = sentence_row.section
                    df_resources.rename(columns={'@URI':'URI','@types':'types','@surfaceForm':'surfaceForm','@support':'support','@offset':'offset',
                                                 '@similarityScore':'similarityScore','@percentageOfSecondRank':'percentageOfSecondRank'}, inplace=True)
                    if not file_exists:
                        df_resources.to_csv('cacheSpotlightResponse/'+file_name.file_name,index=False)
                    else:
                        df_resources.to_csv('cacheSpotlightResponse/'+file_name.file_name,mode='a',index=False,header=False)

            except Exception as ex:
                print("All entities ****")
                if hasattr(ex, 'message'):
                    print(ex.message)
                else:
                    print(ex)
        time.sleep(2)
    time.sleep(10)

103566.csv


In [17]:
# files_emptyTypes = [f for f in os.listdir('cacheSpotlightResponse') if not f.startswith('.')]
# # # parse to dataframe
# df_files_emptyTypes= pd.DataFrame(files_emptyTypes, columns=['file_name'])

# # df_files.to_csv('totalBiographiesEntities.csv',index=False)
# df_files_emptyTypes = df_files_emptyTypes[df_files_emptyTypes['file_name'].str.contains('_emptyTypes')]
# # df_files_emptyTypes = df_files_emptyTypes.query("file_name=='1557508_emptyTypes.csv'")
# df_files_emptyTypes['file_name'] = df_files_emptyTypes['file_name'].str.replace('_emptyTypes','')

# df_files_emptyTypes.to_csv('emptyTypesList.csv',index=False)

# df_files_emptyTypes.info()
# df_files_emptyTypes.head()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 8627 entries, 1 to 17262
Data columns (total 1 columns):
 #   Column     Non-Null Count  Dtype 
---  ------     --------------  ----- 
 0   file_name  8627 non-null   object
dtypes: object(1)
memory usage: 134.8+ KB


file_name
1  10002116.csv
3   1000228.csv
5  10004137.csv
7   1000522.csv
9   1000539.csv

In [5]:
# df_master_empty_entities = pd.DataFrame(columns=['entity','URI','file_name'])
# file_number = 0
# for file_name_item in df_files_emptyTypes.itertuples():
    
#     # df_entities = pd.read_csv('cacheSpotlightResponse/'+file_name_item.file_name.replace('_emptyTypes',''))
#     df_entities = pd.read_csv('cacheSpotlightResponse/'+file_name_item.file_name, usecols=['entity','URI'])
    
#     print(len(df_entities))
#     # df_entities = df_entities.loc[df_entities['types'].isna()] 
#     # df_entities = df_entities.drop(['algebra', 'chemistry'], axis=1)
#     df_entities.drop_duplicates(subset=['entity','URI'],keep='first',inplace=True)
    
#     if os.path.isfile('cacheSpotlightResponse/emptyTypes_master.csv'):
#         # read file, and verify new entries are not already in the file
#         df_master_empty_entities = pd.read_csv('cacheSpotlightResponse/emptyTypes_master.csv')
#         df=df_master_empty_entities.merge(df_entities, on='entity',how='right')
#         df.info()
#         df = df.loc[df['URI_x'].isna()]
#         print(len(df))
        
#         if len(df)>0:
#             df = df.rename(columns={'URI_y':'URI'})
#             df = df.loc[:, ["URI","entity"]]

#             df['file_name']='emptyTypes_{}.csv'.format(str(file_number))

#             df.to_csv('cacheSpotlightResponse/emptyTypes_master.csv',mode='a',index=False,header=False)
            
#             df_entities = pd.read_csv('cacheSpotlightResponse/'+file_name_item.file_name)
#             df_entities.to_csv('cacheSpotlightResponse/emptyTypes_'+str(file_number)+'.csv',index=False)
            
#             file_number += 1
#     else:
#         df_entities['file_name']='emptyTypes_{}.csv'.format(str(file_number))
#         df_entities.to_csv('cacheSpotlightResponse/emptyTypes_master.csv',index=False)
        
#         df_entities = pd.read_csv('cacheSpotlightResponse/'+file_name_item.file_name)
#         df_entities.to_csv('cacheSpotlightResponse/emptyTypes_'+str(file_number)+'.csv',index=False)
        
#         file_number += 1

# # df_entities.info()
# # df_entities.head()

5407
856
<class 'pandas.core.frame.DataFrame'>
Int64Index: 33 entries, 0 to 32
Data columns (total 4 columns):
 #   Column     Non-Null Count  Dtype 
---  ------     --------------  ----- 
 0   URI_x      1 non-null      object
 1   entity     33 non-null     object
 2   file_name  1 non-null      object
 3   URI_y      33 non-null     object
dtypes: object(4)
memory usage: 1.3+ KB
32
460
<class 'pandas.core.frame.DataFrame'>
Int64Index: 46 entries, 0 to 45
Data columns (total 4 columns):
 #   Column     Non-Null Count  Dtype 
---  ------     --------------  ----- 
 0   URI_x      1 non-null      object
 1   entity     46 non-null     object
 2   file_name  1 non-null      object
 3   URI_y      46 non-null     object
dtypes: object(4)
memory usage: 1.8+ KB
45
621
<class 'pandas.core.frame.DataFrame'>
Int64Index: 60 entries, 0 to 59
Data columns (total 4 columns):
 #   Column     Non-Null Count  Dtype 
---  ------     --------------  ----- 
 0   URI_x      3 non-null      object
 1   e

## 3. Query entities without the type

In [6]:
# Adding process to query entities without the type
        # filter only rows without category
# use chunk to load a small number of files in memory
        
if os.path.isfile('emptyTypesList.csv'):
    # read the files already checked for empty entities
    df_empty_entities = pd.read_csv('emptyTypesList.csv')
else:
    df_empty_entities = pd.DataFrame(columns=['file_name'])
    df_empty_entities.to_csv('emptyTypesList.csv',index=False)
# retrieve the next id to store the empty entitites
if os.path.isfile('cacheSpotlightResponse/emptyTypes_master.csv'):
    df_master = pd.read_csv('cacheSpotlightResponse/emptyTypes_master.csv')
    df_master['id'] = df_master['file_name'].str.replace('emptyTypes_','')
    df_master['id'] = df_master['id'].str.replace('.csv','')
    df_master['id'] = df_master['id'].astype(str).astype(int)
    df_master = df_master.sort_values(by='id', ascending=False)
    last_file_id = df_master['id'].loc[df_master.index[0]]
    last_file_id = int(last_file_id)
else:
    df_master = pd.DataFrame(columns=['entity','URI','file_name'])
    df_master.to_csv('cacheSpotlightResponse/emptyTypes_master.csv',index=False)
    last_file_id = 0

print(last_file_id)

for chunk in pd.read_csv('totalBiographiesEntities.csv', chunksize=10):
    df_files = pd.DataFrame()
    df_files['file_name'] = chunk['file_name']
    
    for file_name_item in df_files.itertuples():
        print(file_name_item.file_name)
        # if next file is in emptyTypeList means already review the empty types, if not in list then continue
        if len(df_empty_entities[df_empty_entities['file_name'].str.contains(file_name_item.file_name)])==0:
            # print("Not in empty entities file")
            # read response from dbpediasportlight cache
            df_bio = pd.read_csv('cacheSpotlightResponse/'+file_name_item.file_name)
            # filter rows with types == NA
            df = df_bio.loc[df_bio['types'].isna()] 
            # drop row with same URI
            df.drop_duplicates(subset=['URI'],keep='first',inplace=True)
            # print("Total empty entities: "+str(len(df)))
            
            if not df.empty:
                df = df.rename(columns={'surfaceForm':'entity'})
                # df_temp = df.loc[:, ["URI","entity"]]
            
                if os.path.isfile('cacheSpotlightResponse/emptyTypes_master.csv'):
                    # read file, and verify new entries are not already in the file
                    df_master_empty_entities = pd.read_csv('cacheSpotlightResponse/emptyTypes_master.csv')
                    df_merge=df_master_empty_entities.merge(df, on='URI',how='right')
                    # df_merge.info()
                    # filter the rows that are not in the master file
                    df_merge = df_merge.loc[df_merge['entity_x'].isna()]
                    print("Total to query after verifying master empty entities: "+str(len(df_merge)))

                    if len(df_merge)>0:
                        last_file_id +=1
                        df_merge = df_merge.rename(columns={'entity_y':'entity'})

                        for item in df_merge.itertuples():
                            df_results = pd.DataFrame()
                            query_text = "SELECT * WHERE { <" + item.URI + "> <http://www.w3.org/1999/02/22-rdf-syntax-ns#type>  ?o }"
                            try:
                                # Execute query against sparql endpoint, query types
                                results = executeQueryDbpedia(query_text).json()
                                # print(results)
                                # if query returns a response
                                if 'results' in results:
                                    # to obtain the list of types
                                    res_1 = list(map(itemgetter('o'), results['results']['bindings']))
                                    res_2 = list(map(itemgetter('value'), res_1))

                                    df_results['types'] = res_2
                                    df_results['URI'] = item.URI
                                    df_results['entity'] = item.entity
                                    df_results['support'] = item.support
                                    df_results['offset'] = item.offset
                                    df_results['similarityScore'] = item.similarityScore
                                    df_results['percentageOfSecondRank'] = item.percentageOfSecondRank

                                    df_results['sentenceIndex']=item.sentenceIndex
                                    df_results['paragraphIndex'] = item.paragraphIndex
                                    df_results['section'] = item.section
                                    
                                    df_new_master_row = pd.DataFrame({'URI':[item.URI],'entity':[item.entity],
                                                                                  'file_name':['emptyTypes_{}.csv'.format(str(last_file_id))]})
                                    df_new_master_row.to_csv('cacheSpotlightResponse/emptyTypes_master.csv',mode='a',
                                                         index=False,header=False)
                                    # print("Saved master file: " + str(last_file_id) + ". Len: " + str(len(df_new_master_row)))

                                    file_exists = os.path.isfile('cacheSpotlightResponse/emptyTypes_'+str(last_file_id)+'.csv')
                                    if not file_exists:
                                        df_results.to_csv('cacheSpotlightResponse/emptyTypes_'+str(last_file_id)+'.csv',index=False)
                                    else:
                                        df_results.to_csv('cacheSpotlightResponse/emptyTypes_'+str(last_file_id)+'.csv',mode='a',
                                                         index=False,header=False)
                            except Exception as ex:
                                print("Blank type: ****")
                                if hasattr(ex, 'message'):
                                    print(ex.message)
                                else:
                                    print(ex)
            df_file_checked = pd.DataFrame({'file_name':[file_name_item.file_name]})
            df_file_checked.to_csv('emptyTypesList.csv',mode='a',index=False,header=False)
                                    
            # print("Saved emptyTypesList: " + file_name_item.file_name + ". Len: " + str(len(df_file_checked)))

/tmp/ipykernel_69/802423279.py:10: FutureWarning: The default value of regex will change from True to False in a future version.
  df_master['id'] = df_master['id'].str.replace('.csv','')


17669
10002116.csv
1000228.csv
10004137.csv
1000522.csv
1000539.csv
10006387.csv
1000684.csv
10009278.csv
100097.csv
1001128.csv
100113.csv
100122.csv
10012696.csv
10012995.csv
1001319.csv
10014446.csv
1001551.csv
100156.csv
10015870.csv
100161.csv
10016688.csv
10018259.csv
1001915.csv
100196.csv
10020104.csv
10021200.csv
1002229.csv
1002377.csv
1002541.csv
100273.csv
10027922.csv
10028394.csv
100285.csv
1003230.csv
10033557.csv
100339.csv
10034984.csv
10036685.csv
1003860.csv
100394.csv
10039413.csv
1003976.csv
100405.csv
1004050.csv
1004059.csv
1004126.csv
10041590.csv
10043034.csv
1004324.csv
10043922.csv
1004777.csv
100487.csv
10049.csv
10049028.csv
10049441.csv
1005009.csv
100506.csv
1005079.csv
1005113.csv
1005131.csv
10054774.csv
10056075.csv
1005872.csv
1006211.csv
10062845.csv
1006290.csv
1006384.csv
100641.csv
1006647.csv
1006900.csv
100691.csv
10069248.csv
1006985.csv
1007007.csv
10070358.csv
10071316.csv
1007220.csv
10072546.csv
1007264.csv
10073280.csv
10074446.csv
1007764

/opt/conda/lib/python3.9/site-packages/pandas/util/_decorators.py:311: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return func(*args, **kwargs)


Total to query after verifying master empty entities: 0
389667.csv
Total to query after verifying master empty entities: 6
389670.csv
Total to query after verifying master empty entities: 1
38976337.csv
Total to query after verifying master empty entities: 0
38978684.csv
Total to query after verifying master empty entities: 0
38978851.csv
38979300.csv
Total to query after verifying master empty entities: 3
38982310.csv
Total to query after verifying master empty entities: 2
389825.csv
Total to query after verifying master empty entities: 2
38982886.csv
Total to query after verifying master empty entities: 1
3899139.csv
Total to query after verifying master empty entities: 7
38993440.csv
Total to query after verifying master empty entities: 0
38994119.csv
Total to query after verifying master empty entities: 11
3899439.csv
Total to query after verifying master empty entities: 1
38999789.csv
Total to query after verifying master empty entities: 0
3900107.csv
Total to query after verifyin